In [1]:
import numpy as np
import pandas as pd
import time

In [2]:
import csv
with open('Q Learning data.csv', newline='') as csvfile:
    rows = csv.reader(csvfile)
    for row in rows:
        print(row)

['music', 'times']
['0', '20']
['1', '5']
['2', '10']
['3', '17']
['4', '13']
['5', '15']
['6', '10']
['7', '30']
['8', '0']
['9', '30']
['10', '22']
['11', '25']
['12', '30']
['13', '7']
['14', '30']
['15', '1']
['16', '2']
['17', '5']
['18', '14']
['19', '0']


In [3]:
df = pd.read_csv('Q Learning data.csv')

In [4]:
len(df)

20

In [5]:
#music = ["M1", "M2", "M3", "M4", "M5", "M6", "M7", "M8", "M9", "M10", "M11", "M12", "M13", "M14", "M15", "M16", "M17", "M18", "M19", "M20"]
music = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17 ,18, 19, 20]
times = [20, 5, 10, 17, 13, 15, 10, 30, 0, 30, 22, 25, 30, 7, 30, 1, 2, 5, 14, 0]

music_dict = {"music": music, "times": times}

music_df = pd.DataFrame(music_dict)

In [6]:
music_df

music  times
0       1     20
1       2      5
2       3     10
3       4     17
4       5     13
5       6     15
6       7     10
7       8     30
8       9      0
9      10     30
10     11     22
11     12     25
12     13     30
13     14      7
14     15     30
15     16      1
16     17      2
17     18      5
18     19     14
19     20      0

In [7]:
N_STATES = 20   # 1维世界的寬度
ACTIONS = ['dislike', 'click', 'listen', 'like']     # 探索者的可用動作
EPSILON = 0.9   # 貪婪度 greedy
ALPHA = 0.1     # 學習率
GAMMA = 0.9    # 獎勵遞減值
MAX_EPISODES = 13   # 最大回合數
FRESH_TIME = 0.3    # 移動尖閣時間

In [8]:
def build_q_table(n_states, actions):
    table = pd.DataFrame(
        np.zeros((n_states, len(actions))),     # q_table初始全0
        columns=actions,    # columns對應的是行為名稱
    )
    return table

In [9]:
build_q_table(N_STATES, ACTIONS)

dislike  click  listen  like
0       0.0    0.0     0.0   0.0
1       0.0    0.0     0.0   0.0
2       0.0    0.0     0.0   0.0
3       0.0    0.0     0.0   0.0
4       0.0    0.0     0.0   0.0
5       0.0    0.0     0.0   0.0
6       0.0    0.0     0.0   0.0
7       0.0    0.0     0.0   0.0
8       0.0    0.0     0.0   0.0
9       0.0    0.0     0.0   0.0
10      0.0    0.0     0.0   0.0
11      0.0    0.0     0.0   0.0
12      0.0    0.0     0.0   0.0
13      0.0    0.0     0.0   0.0
14      0.0    0.0     0.0   0.0
15      0.0    0.0     0.0   0.0
16      0.0    0.0     0.0   0.0
17      0.0    0.0     0.0   0.0
18      0.0    0.0     0.0   0.0
19      0.0    0.0     0.0   0.0

In [10]:
A_List = []
for i in range (len(music_df)):
    times = music_df["times"][i]
    if times == 0:
        A = 'dislike'
        A_List.append(A)
    elif 0 < times < 10:
        A = 'click'
        A_List.append(A)
    elif 10 <= times < 30:
        A = 'listen'
        A_List.append(A)
    elif times >= 30:
        A = 'like'
        A_List.append(A)
print(A_List)

['listen', 'click', 'listen', 'listen', 'listen', 'listen', 'listen', 'like', 'dislike', 'like', 'listen', 'listen', 'like', 'click', 'like', 'click', 'click', 'click', 'listen', 'dislike']


In [11]:
# 在某個state地點，選擇行為
def choose_action(state, q_table):
    state_actions = q_table.iloc[state, :]  # 選出這個state的所有action值
    #print('state_actions:','\n',state_actions)
    if (np.random.uniform() > EPSILON) or (state_actions.all() == 0):  # 非貪婪 or 或者這個 state 還沒有探索過
        action_name = np.random.choice(ACTIONS)
    else:
        action_name = state_actions.argmax()    # 貪婪模式
    return action_name

In [12]:
def action(times):
    if times == 0:
        A = 'dislike'
        A_List.append(A)
    elif 0 < times < 10:
        A = 'click'
        A_List.append(A)
    elif 10 <= times < 30:
        A = 'listen'
        A_List.append(A)
    elif times >= 30:
        A = 'like'
        A_List.append(A)
    return A

In [13]:
def get_env_feedback(S,A):
    
    if A == 'dislike':
        if S == 0:   # terminate
            S_ = S # dislike扣兩分
            R = -2
        else:
            S_ = S - 1
            R = -2

    elif A == 'click':
        R = -1
        if S == 0:
            S_ = S 
        else:
            S_ = S - 1

    elif A == 'listen':
        R = 1
        if S == 0:
            S_ = S 
        else:
            S_ = S - 1

    elif A == 'like':
        R = 2
        if S == N_STATES - 1:
            S_ = 'terminal'
        else:
            S_ = S + 1
    #print('播放程度：',A)
    return S_, R

In [14]:
def update_env(S, episode, step_counter):
    # This is how environment be updated
    env_list = ['-']*(N_STATES-1) + ['T']   # '---------T' our environment
    
    if S == 'terminal':
        interaction = 'Episode %s: total_steps = %s' % (episode+1, step_counter)
        print(interaction)
        print('=====================================================')
        #print('\r{}'.format(interaction), end='')
        #time.sleep(2)
        #print('\r                                ', end='')
    
    else:
        env_list[S] = 'o'
        interaction = ''.join(env_list)
        print(interaction)
        #print('\r{}'.format(interaction), end='')
        #time.sleep(FRESH_TIME)

In [15]:
def rl():
    q_table = build_q_table(N_STATES, ACTIONS)  # 初始 q table
    
    for i in range(len(music_df)):     # 回合數
        #times = music_df["times"][i]
        step_counter = 0
        S = music_df["music"][0] - 1   # 回合初始位置
        #print(S)
        
        is_terminated = False   # 是否回合結束
        #update_env(S, episode, step_counter)    # 環境更新
        
        while not is_terminated:
            #for i in range(len(music_df)):
                #times = music_df["times"][i]
                #action(times)
            #print("選行為：", A)
            
            A = choose_action(S, q_table)   # 選行為
            print("選行為：", A)
            S_, R = get_env_feedback(S,A)  # 實施行為並得到環境的反饋
            print("S_: ",S_)
            print("R: ",R)
            q_predict = q_table.loc[S, A]    # 估算的(狀態-行為)值
            
            if S_ != 'terminal':
                q_target = R + GAMMA * q_table.iloc[S_, :].max()   # 實際的(狀態-行為)值 (回合沒結束)
            else:
                q_target = R     #  實際的(狀態-行為)值 (回合結束)
                is_terminated = True    # terminate this episode

            q_table.loc[S, A] += ALPHA * (q_target - q_predict)  #  q_table更新
            S = S_  # 移動到下一個 state
            #print(q_table)
            
            #update_env(S, episode, step_counter + 1)  # 環境更新

            step_counter += 1
    
    return q_table

In [16]:
if __name__ == "__main__":
    q_table = rl()
    print('=====DONE=====')

選行為： listen
S_:  0
R:  1
選行為： like
S_:  1
R:  2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： dislike
S_:  0
R:  -2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： dislike
S_:  0
R:  -2
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： like
S_:  1
R:  2
選行為： dislike
S_:  0
R:  -2
選行為： listen
S_:  0
R:  1
選行為： like
S_:  1
R:  2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： dislike
S_:  0
R:  -2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: FutureWarning: 'argmax' is deprecated, use 'idxmax' instead. The behavior of 'argmax'
will be corrected to return the positional maximum in the future.
Use 'series.values.argmax' to get the position of the maximum now.
  


 listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： dislike
S_:  0
R:  -2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行

R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： dislike
S_:  0
R:  -2
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  

選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： click
S_:  0
R:  -1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1
選行為： listen
S_:  0
R:  1


...

S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： click
S_:  17
R:  -1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen


選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： listen
S_:  16
R:  1
選行為： like
S_:  17
R:  2
選行為： like
S_:  18
R:  2
選行為： dislike
S_:  17
R:  -2
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  

S_:  17
R:  2
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： dislike
S_:  17
R:  -2
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： listen
S_:  16
R:  1
選行為： like
S_:  17
R:  2
選行為： dislike
S_:  16
R:  -2
選行為： like
S_:  17
R:  2
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： lis

S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen
S_:  17
R:  1
選行為： like
S_:  18
R:  2
選行為： listen


選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： listen
S_:  9
R:  1
選行為： dislike
S_:  8
R:  -2
選行為： like
S_:  9
R:  2
選行為： like
S_:  10
R:  2
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： dislike
S_:  9
R:  -2
選行為： like
S_:  10
R:  2
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： dislike
S_:  9
R:  -2
選行為： like
S_:  10
R:  2
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： like
S_:  11
R:  2
選行為： listen
S_:  10
R:  1
選行為： click
S_:  9
R:  -1
選行為： dislike
S_:  8
R:  

In [17]:
print('\r\nQ-table:')
q_table


Q-table:


dislike      click     listen       like
0   11.892618  12.960940  14.823961  16.782059
1   12.155952  13.150138  15.157314  16.835038
2   12.164378  12.531414  15.042939  16.791230
3   12.272663  13.294839  15.319352  16.741929
4   12.194058  13.300136  15.264876  16.695733
5   12.204593  13.273826  15.240892  16.630921
6   12.245973  13.208096  15.214398  16.516274
7   12.194261  13.171967  15.212888  16.331151
8   12.256020  13.264128  15.242867  16.105641
9   12.241355  13.199219  15.211118  15.734815
10  12.048659  13.087172  15.026341  15.262800
11  10.514219  11.885336  14.736480   8.811657
12   1.121359   2.525403   0.330578  12.024513
13  -0.164180   0.076561   0.156306  15.493466
14   0.925686   0.454394   2.754805  16.527866
15  10.373830   8.627355  11.229910  16.163578
16  12.545468  13.545946  15.546056  15.749669
17  12.163158  13.163158  15.163158  15.370537
18  11.739370  12.754088  14.744123  14.996619
19  11.282198  11.073438  14.468129   1.756847